In [48]:
%reload_ext autoreload
%autoreload 2

import os
import acled_conflict_analysis as acled
from acled_conflict_analysis import visuals
from acled_conflict_analysis import analysis
from acled_conflict_analysis import extraction

from datetime import date
from datetime import datetime


In [2]:
countries_of_interest = ["Iran"]
START_DATE = "2012-01-01"
END_DATE = "2024-05-10"

In [49]:
data = extraction.acled_api(
    email_address=os.environ.get("ACLED_EMAIL"),
    access_key=os.environ.get("ACLED_KEY"),
    countries=countries_of_interest,
    start_date=START_DATE,
    end_date=END_DATE
)


In [5]:
analysis.data_type_conversion(data)

In [26]:
conflict_monthly = analysis.get_acled_by_group(data, columns=['latitude', 'longitude'], freq='MS')
conflict_yearly = analysis.get_acled_by_group(data, columns=['latitude', 'longitude'], freq='YS')
conflict_yearly_national = analysis.get_acled_by_group(data, columns=['country'], freq='Y')
conflict_sub_event_type = analysis.get_acled_by_group(data, columns = ['event_type', 'sub_event_type'], freq='MS')
conflict_event_type = analysis.get_acled_by_group(data, columns = ['country','event_type'], freq='MS')

c:\WBG\Anaconda3\envs\data-goods\Lib\site-packages\acled_conflict_analysis\analysis.py:39: FutureWarning: 'Y' is deprecated and will be removed in a future version, please use 'YE' instead.


In [15]:
events_dict = {datetime(2023, 10, 7):'First Attack on Gaza',
    datetime(2023, 11, 17):'First Attack on the Red Sea',
               }

In [35]:
# output_file("bokeh_plot.html")
output_notebook()


tabs = []

for idx, type in enumerate(["nrFatalities", "nrEvents"]):
    tabs.append(
        TabPanel(
            child=visuals.get_line_plot(
                conflict_yearly_national,
                f"Line Plot",
                "Source: ACLED. Accessed 19th September 2024",
                subtitle="",
                category="country",
                measure=type,
                events_dict = events_dict
            ),
            title=type.capitalize(),
        )
    )

tabs = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs, warn_on_missing_glyphs=False)

Loading BokehJS ...

### Map

In [26]:
visuals.get_animated_map(conflict_monthly, 'Iran', 50,'nrFatalities','P1M')

In [28]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from bokeh.models import Panel, Tabs

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}

measure = 'nrEvents'

show(
    visuals.get_bar_chart(
        conflict_monthly,
        f"Bar Chart e.g., Monthly Reported {measure_names[measure]}",
        f"Source: ACLED. Accessed date {datetime.today().date().isoformat()}",
        subtitle="",
        category=None,
        measure=measure,
        color_code=measure_colors[measure],
        events_dict=events_dict
    )
)

Loading BokehJS ...

In [19]:
from bokeh.plotting import show, output_notebook
import bokeh
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from bokeh.models import Panel, Tabs, TabPanel

output_notebook()

bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)


tabs = []
measure_names = {
    "nrEvents": "Number of Conflict Events",
    "nrFatalities": "Number of Fatalities",
}
measure_colors = {"nrEvents": "#4E79A7", "nrFatalities": "#F28E2B"}
# acled_adm0 = get_acled_by_admin(syria_adm2_crs, acled, columns = ['ADM2_EN', 'ADM1_EN'])
for category_type in list(conflict_event_type["event_type"].unique()):
    tabs.append(
        TabPanel(
            child=visuals.get_bar_chart(
                conflict_event_type,
                f"Multi Tab Chart by Category e.g., {category_type}",
                "Source: ACLED. Accessed date {datetime.today().date().isoformat()}",
                subtitle="",
                category="event_type",
                measure="nrEvents",
                color_code=measure_colors["nrEvents"],
                category_value=category_type,
                events_dict=events_dict
            ),
            title=category_type.title(),
        )
    )

tabs = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs, warn_on_missing_glyphs=False)

Loading BokehJS ...

In [25]:
output_notebook()
from bokeh.core.validation.warnings import EMPTY_LAYOUT, MISSING_RENDERERS
from bokeh.models import Panel, Tabs
from bokeh.palettes import Category10  # Import Bokeh color palette
import random


bokeh.core.validation.silence(EMPTY_LAYOUT, True)
bokeh.core.validation.silence(MISSING_RENDERERS, True)

tabs = []

for category_type in list(conflict_sub_event_type["event_type"].unique()):

    df = conflict_sub_event_type[
                    conflict_sub_event_type["event_type"] == category_type
                ]
    event_types = list(df["sub_event_type"].unique())

    num_event_types = len(df["sub_event_type"].unique())
    if num_event_types < 10:
        # If there are fewer than 10 event types, randomly pick that many colors from Category10[10]
        colors = random.sample(Category10[10], num_event_types)
    else:
        # If there are 10 or more event types, use Category10[10] directly
        colors = Category10[10]

    tabs.append(
        TabPanel(
            child=visuals.get_stacked_bar_chart(
                df,
                f"Stacked Bar Chart",
                source_text=f"Source: ACLED. Accessed ",
                date_column="event_date",
                categories=event_types,
                measure="nrEvents",
                category_column='sub_event_type',
                colors=colors,
                events_dict=events_dict
            ),
            title=category_type.title(),
        )
    )

tabs = Tabs(tabs=tabs, sizing_mode="scale_both")
show(tabs, warn_on_missing_glyphs=False)

Loading BokehJS ...